**Steps involved in the project**  

Exploratory data analysis
Data cleaning  
Text preprocessing  
Feature extraction
Training the text classification model  
Creating a recommedation systems (User based and Item Based choose the bestone)  
Evaluating the model and recommedation system using the Test data   
Create flask application  
Deploy the application to heroku platform   

In [1]:
!pip install ydata_profiling

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 400.1/400.1 kB 30.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 24.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 687.8/687.8 kB 44.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.3/43.3 kB 3.5 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=8124fa773eacb7fda4d9f131bf662d4fa88da0455dd52dc34b30f6c9913fefde
  Stored in directory: /root/.cache/pip/wheels/8d/55/1a/19cd535375ed1ede0c996405ebffe34b196d78e2d9545723a2
Successfully built htmlmin


In [2]:
from ydata_profiling import ProfileReport

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
mydrive_path='/content/drive/MyDrive/'

In [5]:
import numpy as np
import pandas as pd
import re, nltk, spacy, string
import en_core_web_sm
nlp = en_core_web_sm.load()
from ydata_profiling import ProfileReport
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import classification_report,roc_auc_score,confusion_matrix,f1_score,precision_score,accuracy_score
from sklearn.metrics import pairwise_distances
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier,GradientBoostingClassifier
from sklearn.model_selection import train_test_split,GridSearchCV,RandomizedSearchCV,cross_val_score
from sklearn.preprocessing import MinMaxScaler
import xgboost as xgb
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger_eng')
from collections import Counter
from imblearn.over_sampling import SMOTE
from sklearn.naive_bayes import MultinomialNB
from xgboost import XGBClassifier
import pickle

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger_eng.zip.


In [6]:
master_df = pd.read_csv(mydrive_path+'sample30.csv')
df=master_df.copy()
df.sample(5)

id              brand  \
5506   AVpf0thK1cnluZ0-r8vR       Warner Bros.   
10576  AVpf3VOfilAPnD_xjpun             Clorox   
20579  AVpfJP1C1cnluZ0-e3Xy             Clorox   
25687  AVpfPaoqLJeJML435Xk9  Warner Home Video   
25979  AVpfPaoqLJeJML435Xk9  Warner Home Video   

                                              categories       manufacturer  \
5506   Movies, Music & Books,Movies,New Movie Release...  Warner Home Video   
10576  Household Essentials,Cleaning Supplies,Kitchen...             Clorox   
20579  Household Chemicals,Household Cleaners,Bath & ...     AmazonUs/CLOO7   
25687  Movies, Music & Books,Movies,Action & Adventur...               Test   
25979  Movies, Music & Books,Movies,Action & Adventur...               Test   

                                                    name  \
5506                 100:Complete First Season (blu-Ray)   
10576  Clorox Disinfecting Wipes Value Pack Scented 1...   
20579               Clorox Disinfecting Bathroom Cleaner   
25687  Godzilla 3d Includes Digital Copy Ultraviolet ...   
25979  Godzilla 3d Includes Digital Copy Ultraviolet ...   

                   reviews_date reviews_didPurchase reviews_doRecommend  \
5506   2015-08-10T00:00:00.000Z                 NaN                True   
10576  2014-12-03T00:00:00.000Z               False                True   
20579  2012-01-26T05:06:55.000Z                 NaN                True   
25687  2014-11-06T00:00:00.000Z                 NaN                True   
25979  2014-12-29T00:00:00.000Z                 NaN                True   

       reviews_rating                                       reviews_text  \
5506                5  Great show. Nice that it comes with a digital ...   
10576               5  I love and use this product to help keep my ki...   
20579               5  i absolutely love this product, it is great fo...   
25687               5  Love this re-make. Which is why I love it. It'...   
25979               5  This is a fun movie!! Getting it so cheaply on...   

              reviews_title reviews_userCity reviews_userProvince  \
5506             Great show              NaN                  NaN   
10576  Convenient and clean              NaN                  NaN   
20579     Best Product Ever        Jamestown                   OH   
25687         It's Godzilla              NaN                  NaN   
25979           Fun movie!!              NaN                  NaN   

      reviews_username user_sentiment  
5506        movielover       Positive  
10576          mnsparx       Positive  
20579        hashbrown       Positive  
25687           damase       Positive  
25979       homeworker       Positive

**EDA**

In [7]:
profile = ProfileReport(
    df,
    title="EDA Report - Product Reviews",
    explorative=True,
    missing_diagrams={"heatmap": True},
    samples={"head": 5}
)

# Save report to HTML
profile.to_file("eda_report_product_reviews.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 15/15 [00:03<00:00,  4.74it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

**DATA Cleaning**

since over 93% values are missing dropping fields

In [8]:
df = df.drop(columns=['reviews_userCity','reviews_userProvince'],axis=1)

In [9]:
df[['reviews_rating', 'user_sentiment']]

reviews_rating user_sentiment
0                   5       Positive
1                   5       Positive
2                   5       Positive
3                   1       Negative
4                   1       Negative
...               ...            ...
29995               5       Positive
29996               5       Positive
29997               5       Positive
29998               5       Positive
29999               5       Positive

[30000 rows x 2 columns]

In [10]:
df[(df['reviews_rating'] <= 2) & (df['user_sentiment'] == 'Positive')][['reviews_rating', 'user_sentiment', 'reviews_text']]

reviews_rating user_sentiment  \
9                   1       Positive   
11                  1       Positive   
14                  1       Positive   
54                  1       Positive   
56                  1       Positive   
...               ...            ...   
28869               2       Positive   
28870               2       Positive   
28871               2       Positive   
28872               2       Positive   
28873               2       Positive   

                                            reviews_text  
9      Got as a surprise for my husband there is noth...  
11     Purchased this thinking it would have some sor...  
14     First time purchase of this type of product. M...  
54     I used (and loved) this product for several ye...  
56     I am so disappointed! I have used this product...  
...                                                  ...  
28869  This was the last step out of the three step p...  
28870  I have been a big LOral fan, using their produ...  
28871  Despite using this with the line's hair mask a...  
28872  I tried out this whole set.i wanted it to work...  
28873  Received this product from Influenster to test...  

[1067 rows x 3 columns]

In [11]:
df[(df['reviews_rating'] >= 4) & (df['user_sentiment'] == 'Negative')][['reviews_rating', 'user_sentiment', 'reviews_text']]

reviews_rating user_sentiment  \
92                  4       Negative   
96                  4       Negative   
100                 4       Negative   
106                 4       Negative   
117                 4       Negative   
...               ...            ...   
29818               5       Negative   
29855               5       Negative   
29858               5       Negative   
29862               5       Negative   
29941               5       Negative   

                                            reviews_text  
92     It hydrates my skin. It is not too thick and h...  
96     In only a week I can see the difference in my ...  
100    This product has made my skin smoother and sup...  
106    I like to use this cream on my neck and collar...  
117    I finally found a moisturizing product that wi...  
...                                                  ...  
29818  I received a complimentary sample of this prod...  
29855  This has prolonged the color in my hair! Not o...  
29858  This conditioner makes my hair very soft witho...  
29862  This conditioner has become a staple in my hai...  
29941  It's very difficult to find a conditioner that...  

[2410 rows x 3 columns]

In [12]:
pd.crosstab(df["user_sentiment"], df["reviews_rating"], margins=True)

reviews_rating     1    2     3     4      5    All
user_sentiment                                     
Negative         597  140   220   550   1860   3367
Positive         787  280  1125  5470  18970  26632
All             1384  420  1345  6020  20830  29999

As per the above results, there looks to be mismtach between review_rating and user_sentiment. there are records that have higher user rating but user sentiment is negative and lower user rating but user sentiment is positive. We can either clean up those records or update the target column to the correct user sentiment, so that will be helpful for modelling. Here, updating the user_sentiment to 0 (but was 1) when the reviews_rating is less than 4, and updating the user_sentiment to 1(but was 0), when the reviews_rating is greater than or equal to 4

In [13]:
def review_sentiment_clear(x):
  if x >= 3 :
    return 'Postive'
  elif x > 0 and x < 3  :
    return 'Negative'

In [14]:
df['user_sentiment'] = df['reviews_rating'].apply(review_sentiment_clear)
pd.crosstab(df["user_sentiment"], df["reviews_rating"], margins=True)

reviews_rating     1    2     3     4      5    All
user_sentiment                                     
Negative        1384  420     0     0      0   1804
Postive            0    0  1345  6020  20831  28196
All             1384  420  1345  6020  20831  30000

In [15]:
df = df[~df.reviews_username.isnull()]

**Text Preprocessing for Modelling**

In [16]:
def clean_text(text):
  text = text.lower()
  text = text.strip()
  text = re.sub("\S*\d\S*", "", text)
  text = re.sub('[^A-Za-z]+', ' ', text)
  return text

In [17]:
from nltk.corpus import stopwords
nltk.download('stopwords')
stopword_list= stopwords.words('english')
def remove_stopwords(words):
    new_words = []
    for word in words:
        if word.lower() not in stopword_list:
            new_words.append(word)
    return new_words

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [18]:
def get_wordnet_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

In [19]:
def lemmatize_verbs(words):
  lemmatizer = WordNetLemmatizer()
  pos_tags=nltk.pos_tag(words) # Get POS tags
  lemmas = []
  for word,pos in pos_tags:
    tag = get_wordnet_pos(pos)
    lemma=lemmatizer.lemmatize(word,pos=tag)
    lemmas.append(lemma)
  return lemmas

In [20]:
def textprocessing(input_text):
  text = clean_text(input_text)
  tokens = word_tokenize(text)
  tokens = remove_stopwords(tokens)
  tokens = lemmatize_verbs(tokens)
  return " ".join(tokens)

In [21]:
df_clean = df[['reviews_text', 'user_sentiment']]

In [22]:
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

In [23]:
df_clean.loc[:,"lemmatize_text"] = df_clean["reviews_text"].apply(lambda x: textprocessing(x))
df_clean.head()

/tmp/ipython-input-23-4234650149.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean.loc[:,"lemmatize_text"] = df_clean["reviews_text"].apply(lambda x: textprocessing(x))


reviews_text user_sentiment  \
0  i love this album. it's very good. more to the...        Postive   
1  Good flavor. This review was collected as part...        Postive   
2                                       Good flavor.        Postive   
3  I read through the reviews on here before look...       Negative   
4  My husband bought this gel for us. The gel cau...       Negative   

                                      lemmatize_text  
0  love album good hip hop side current pop sound...  
1          good flavor review collect part promotion  
2                                        good flavor  
3  read review look buy one couple lubricant ulti...  
4  husband buy gel u gel caused irritation felt l...

reviews_text is cleaned to remove stopwords, punctuations,numericals,whitespaces and lemma is derived.

In [24]:
df_clean["user_sentiment"].value_counts(normalize=True)


user_sentiment
Postive     0.940174
Negative    0.059826
Name: proportion, dtype: float64

From above results it is highly unbalanced dataset, so now we create numeric labelling and then SMOTE

In [25]:
df_clean['user_sentiment'] = df_clean['user_sentiment'].map({'Negative':0,'Postive':1})

/tmp/ipython-input-25-2172389176.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean['user_sentiment'] = df_clean['user_sentiment'].map({'Negative':0,'Postive':1})


In [26]:
X = df_clean['lemmatize_text']
y = df_clean['user_sentiment']

In [27]:
tfidf = TfidfVectorizer()
X_tfidf = tfidf.fit_transform(X)
sm = SMOTE(random_state=42)
X_res, y_res = sm.fit_resample(X_tfidf, y)

Verify after SMOTE

In [28]:
print("Before SMOTE:", Counter(y))
print("After SMOTE:", Counter(y_res))

Before SMOTE: Counter({1: 28146, 0: 1791})
After SMOTE: Counter({1: 28146, 0: 28146})


**Model Building**

In [29]:
X_train, X_test, y_train, y_test = train_test_split(X_res, y_res, test_size=0.2, random_state=42)

In [30]:
models = {
    "Logistic Regression": LogisticRegression(max_iter=1000),
    "Naive Bayes": MultinomialNB(),
    "Random Forest": RandomForestClassifier(),
    "XGBoost": XGBClassifier(use_label_encoder=False, eval_metric='logloss'),

}

In [31]:
for name, model in models.items():
  model.fit(X_train,y_train)
  y_pred = model.predict(X_test)
  print(name)
  print(classification_report(y_test,y_pred))

Logistic Regression
              precision    recall  f1-score   support

           0       0.96      0.97      0.97      5616
           1       0.97      0.96      0.97      5643

    accuracy                           0.97     11259
   macro avg       0.97      0.97      0.97     11259
weighted avg       0.97      0.97      0.97     11259

Naive Bayes
              precision    recall  f1-score   support

           0       0.92      0.95      0.93      5616
           1       0.95      0.91      0.93      5643

    accuracy                           0.93     11259
   macro avg       0.93      0.93      0.93     11259
weighted avg       0.93      0.93      0.93     11259

Random Forest
              precision    recall  f1-score   support

           0       0.99      0.99      0.99      5616
           1       0.99      0.99      0.99      5643

    accuracy                           0.99     11259
   macro avg       0.99      0.99      0.99     11259
weighted avg       0.99     

/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [08:35:49] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)


XGBoost
              precision    recall  f1-score   support

           0       0.98      0.97      0.97      5616
           1       0.97      0.98      0.97      5643

    accuracy                           0.97     11259
   macro avg       0.97      0.97      0.97     11259
weighted avg       0.97      0.97      0.97     11259



In [32]:
rf = RandomForestClassifier()
scores = cross_val_score(rf, X_res, y_res, cv=5, scoring='f1')
print("Random Forest CV F1 avg:", np.mean(scores))


Random Forest CV F1 avg: 0.9779702168535037


From above results, Model is not overfitting.Across 5 folds similar results. We can proceed with hypertuning RandomForest Classifier.It has highest accuracy,precision ,recall.

In [33]:
# Phase 1: Quick & coarse search
params1 = {
    'n_estimators': [100, 300],
    'max_depth': [None, 30],
    'min_samples_leaf': [1, 3],
}
grid1 = GridSearchCV(RandomForestClassifier(), params1, cv=3, scoring='f1', n_jobs=-1)
grid1.fit(X_train, y_train)
print("Best from Phase 1:", grid1.best_params_)


Best from Phase 1: {'max_depth': None, 'min_samples_leaf': 1, 'n_estimators': 300}


In [34]:
print("Best F1 Score:", grid1.best_score_)

Best F1 Score: 0.986649963304257


In [35]:
# Save the best estimator from GridSearchCV
with open('rf_model_phase1.pkl', 'wb') as f:
    pickle.dump(grid1.best_estimator_, f)



In [36]:
y_pred = grid1.best_estimator_.predict(X_test)
acc = accuracy_score(y_test, y_pred)
print("Accuracy:", acc)
cm = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:\n", cm)
print("Classification Report:\n", classification_report(y_test, y_pred))

Accuracy: 0.9920952127187139
Confusion Matrix:
 [[5574   42]
 [  47 5596]]
Classification Report:
               precision    recall  f1-score   support

           0       0.99      0.99      0.99      5616
           1       0.99      0.99      0.99      5643

    accuracy                           0.99     11259
   macro avg       0.99      0.99      0.99     11259
weighted avg       0.99      0.99      0.99     11259



In [37]:
from sklearn.metrics import f1_score

y_train_pred = grid1.best_estimator_.predict(X_train)
train_f1 = f1_score(y_train, y_train_pred)
print("Train F1 Score:", train_f1)


Train F1 Score: 0.9999555614806914


**Recommendation System**

Here we are going to try with 2 of the Colloboarative filtering techniques: - User-User Based Approach - Item-Item Based Approach on fresh dataset

User User Recomendation

In [38]:
df = pd.read_csv(mydrive_path+'sample30.csv')
df.head(5)

id            brand  \
0  AV13O1A8GV-KLJ3akUyj  Universal Music   
1  AV14LG0R-jtxr-f38QfS         Lundberg   
2  AV14LG0R-jtxr-f38QfS         Lundberg   
3  AV16khLE-jtxr-f38VFn              K-Y   
4  AV16khLE-jtxr-f38VFn              K-Y   

                                          categories  \
0  Movies, Music & Books,Music,R&b,Movies & TV,Mo...   
1  Food,Packaged Foods,Snacks,Crackers,Snacks, Co...   
2  Food,Packaged Foods,Snacks,Crackers,Snacks, Co...   
3  Personal Care,Medicine Cabinet,Lubricant/Sperm...   
4  Personal Care,Medicine Cabinet,Lubricant/Sperm...   

                         manufacturer  \
0  Universal Music Group / Cash Money   
1                            Lundberg   
2                            Lundberg   
3                                 K-Y   
4                                 K-Y   

                                         name              reviews_date  \
0   Pink Friday: Roman Reloaded Re-Up (w/dvd)  2012-11-30T06:21:45.000Z   
1  Lundberg Organic Cinnamon Toast Rice Cakes  2017-07-09T00:00:00.000Z   
2  Lundberg Organic Cinnamon Toast Rice Cakes  2017-07-09T00:00:00.000Z   
3            K-Y Love Sensuality Pleasure Gel  2016-01-06T00:00:00.000Z   
4            K-Y Love Sensuality Pleasure Gel  2016-12-21T00:00:00.000Z   

  reviews_didPurchase reviews_doRecommend  reviews_rating  \
0                 NaN                 NaN               5   
1                True                 NaN               5   
2                True                 NaN               5   
3               False               False               1   
4               False               False               1   

                                        reviews_text reviews_title  \
0  i love this album. it's very good. more to the...  Just Awesome   
1  Good flavor. This review was collected as part...          Good   
2                                       Good flavor.          Good   
3  I read through the reviews on here before look...  Disappointed   
4  My husband bought this gel for us. The gel cau...    Irritation   

  reviews_userCity reviews_userProvince reviews_username user_sentiment  
0      Los Angeles                  NaN           joshua       Positive  
1              NaN                  NaN        dorothy w       Positive  
2              NaN                  NaN        dorothy w       Positive  
3              NaN                  NaN          rebecca       Negative  
4              NaN                  NaN        walker557       Negative

In [39]:
train,test = train_test_split(df,test_size=0.2,random_state=42)

In [40]:
print (train.shape)
print (test.shape)

(24000, 15)
(6000, 15)


In [41]:
dummy_train = pd.pivot_table(data=train,values='reviews_rating',index='reviews_username',columns='id').fillna(1)
dummy_train.head()

id                AV13O1A8GV-KLJ3akUyj  AV14LG0R-jtxr-f38QfS  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AV16khLE-jtxr-f38VFn  AV1YGDqsGV-KLJ3adc-O  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AV1YIch7GV-KLJ3addeG  AV1YlENIglJLPUi8IHsX  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AV1YmBrdGV-KLJ3adewb  AV1YmDL9vKc47QAVgr7_  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AV1Ymf_rglJLPUi8II2v  AV1Yn94nvKc47QAVgtst  ...  \
reviews_username                                              ...   
00dog3                             1.0                   1.0  ...   
00sab00                            1.0                   1.0  ...   
01impala                           1.0                   1.0  ...   
02dakota                           1.0                   1.0  ...   
02deuce                            1.0                   1.0  ...   

id                AVpfrTyiLJeJML43BrSI  AVpfrfHF1cnluZ0-pRai  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AVpfrgjFLJeJML43BvCc  AVpfs0tUilAPnD_xgqN2  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AVpfshNsLJeJML43CB8q  AVpfthSailAPnD_xg3ON  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0                   1.0   
02deuce                            1.0                   1.0   

id                AVpftikC1cnluZ0-p31V  AVpftymALJeJML43CZ6y  \
reviews_username                                               
00dog3                             1.0                   1.0   
00sab00                            1.0                   1.0   
01impala                           1.0                   1.0   
02dakota                           1.0               

In [42]:
df_pivot = pd.pivot_table(data=train,values='reviews_rating',index='reviews_username',columns='id').fillna(1)

Normalising the rating of the movie for each user around 0 mean

In [43]:
mean = np.nanmean(df_pivot, axis=1)
df_subtracted = (df_pivot.T-mean).T

In [44]:
user_correlation = 1 - pairwise_distances(df_subtracted, metric='cosine')
user_correlation[np.isnan(user_correlation)] = 0
print(user_correlation)

[[ 1.         -0.00378788 -0.00378788 ... -0.00378788 -0.00378788
  -0.00378788]
 [-0.00378788  1.         -0.00378788 ... -0.00378788  1.
  -0.00378788]
 [-0.00378788 -0.00378788  1.         ... -0.00378788 -0.00378788
  -0.00378788]
 ...
 [-0.00378788 -0.00378788 -0.00378788 ...  1.         -0.00378788
   1.        ]
 [-0.00378788  1.         -0.00378788 ... -0.00378788  1.
  -0.00378788]
 [-0.00378788 -0.00378788 -0.00378788 ...  1.         -0.00378788
   1.        ]]


In [45]:
user_correlation[user_correlation < 0] = 0

In [46]:
user_pred_ratings = np.dot(user_correlation,dummy_train.fillna(0))

In [47]:
user_final_rating = np.multiply(user_pred_ratings,df_pivot)
user_final_rating

id                AV13O1A8GV-KLJ3akUyj  AV14LG0R-jtxr-f38QfS  \
reviews_username                                               
00dog3                       17.594371             17.594371   
00sab00                     470.029706            470.029706   
01impala                   2379.426844           2379.426844   
02dakota                   2379.426844           2379.426844   
02deuce                    2379.426844           2379.426844   
...                                ...                   ...   
zuttle                      507.921785            506.401702   
zxcsdfd                    6078.877789           6078.877789   
zxjki                      6078.877789           6078.877789   
zzdiane                     470.029706            470.029706   
zzz1127                    6078.877789           6078.877789   

id                AV16khLE-jtxr-f38VFn  AV1YGDqsGV-KLJ3adc-O  \
reviews_username                                               
00dog3                       17.594371             17.594371   
00sab00                     470.029706            479.103786   
01impala                   2381.265922           2390.219276   
02dakota                   2381.265922           2390.219276   
02deuce                    2381.265922           2390.219276   
...                                ...                   ...   
zuttle                      506.401702            510.380747   
zxcsdfd                    6078.877789           6086.083288   
zxjki                      6078.877789           6086.083288   
zzdiane                     470.029706            479.103786   
zzz1127                    6078.877789           6086.083288   

id                AV1YIch7GV-KLJ3addeG  AV1YlENIglJLPUi8IHsX  \
reviews_username                                               
00dog3                       17.594371             17.594371   
00sab00                     470.029706            470.029706   
01impala                   2379.426844           2379.426844   
02dakota                   2379.426844           2379.426844   
02deuce                    2379.426844           2379.426844   
...                                ...                   ...   
zuttle                      506.401702            506.401702   
zxcsdfd                    6078.877789           6078.877789   
zxjki                      6078.877789           6078.877789   
zzdiane                     470.029706            470.029706   
zzz1127                    6078.877789           6078.877789   

id                AV1YmBrdGV-KLJ3adewb  AV1YmDL9vKc47QAVgr7_  \
reviews_username                                               
00dog3                       17.594371             17.594371   
00sab00                     470.029706            471.376969   
01impala                   2379.426844           2379.426844   
02dakota                   2379.426844           2379.426844   
02deuce                    2379.426844           2379.426844   
...                                ...                   ...   
zuttle                      506.401702            506.401702   
zxcsdfd                    6078.877789           6083.575971   
zxjki                      6078.877789           6083.575971   
zzdiane                     470.029706            471.376969   
zzz1127                    6078.877789           6083.575971   

id                AV1Ymf_rglJLPUi8II2v  AV1Yn94nvKc47QAVgtst  ...  \
reviews_username                                              ...   
00dog3                       17.594371             17.594371  ...   
00sab00                     470.029706            470.029706  ...   
01impala                   2381.446662           2379.426844  ...   
02dakota                   2381.446662           2379.426844  ...   
02deuce                    2381.446662           2379.426844  ...   
...                                ...                   ...  ...   
zuttle                      508.449037            506.401702  ...   
zxcsdfd                    6084.523919         

RMSE Calculation

In [48]:
common = test[test.reviews_username.isin(train.reviews_username)]
common.shape

(1498, 15)

In [49]:
common.head()

id                       brand  \
2308   AVpe41TqilAPnD_xQH3d                         FOX   
22404  AVpfOmKwLJeJML435GM7  Clear Scalp & Hair Therapy   
11311  AVpf3VOfilAPnD_xjpun                      Clorox   
19043  AVpfJP1C1cnluZ0-e3Xy                      Clorox   
9482   AVpf3VOfilAPnD_xjpun                      Clorox   

                                              categories  \
2308   Movies & TV Shows,Movies,Romance,Romantic Come...   
22404  Personal Care,Hair Care,Shampoo,Featured Brand...   
11311  Household Essentials,Cleaning Supplies,Kitchen...   
19043  Household Chemicals,Household Cleaners,Bath & ...   
9482   Household Essentials,Cleaning Supplies,Kitchen...   

                manufacturer  \
2308   Twentieth Century Fox   
22404                  Clear   
11311                 Clorox   
19043         AmazonUs/CLOO7   
9482                  Clorox   

                                                    name  \
2308        Mike Dave Need Wedding Dates (dvd + Digital)   
22404  Clear Scalp & Hair Therapy Total Care Nourishi...   
11311  Clorox Disinfecting Wipes Value Pack Scented 1...   
19043               Clorox Disinfecting Bathroom Cleaner   
9482   Clorox Disinfecting Wipes Value Pack Scented 1...   

                   reviews_date reviews_didPurchase reviews_doRecommend  \
2308   2016-12-14T00:00:00.000Z                 NaN                True   
22404  2016-08-30T00:00:00.000Z               False               False   
11311  2015-01-03T00:00:00.000Z               False                True   
19043  2015-01-14T00:00:00.000Z               False                True   
9482   2012-01-28T03:32:46.000Z                 NaN                True   

       reviews_rating                                       reviews_text  \
2308                5  I have to admit that I was skeptical about see...   
22404               1  I use to LOVE Clear... until it changed it's f...   
11311               5  Awesome product that cleans everything and I h...   
19043               5  Awesome product! Easy to use. Makes the area c...   
9482                5  I use the disinfecting wipes constantly. They ...   

                                 reviews_title reviews_userCity  \
2308                            Awesome movie!              NaN   
22404                        Such a waste....!              NaN   
11311                                  Awesome              NaN   
19043                                   Clorox              NaN   
9482   These Wipes Are Great For Everyday Use.          Georgia   

      reviews_userProvince reviews_username user_sentiment  
2308                   NaN        iplsports       Positive  
22404                  NaN            crysv       Negative  
11311                  NaN      billybob789       Positive  
19043                  NaN             fatz       Positive  
9482                   NaN      natalie4717       Positive

In [50]:
# convert into the user-movie matrix.
common_user_based_matrix=  pd.pivot_table(data=common,values='reviews_rating',index='reviews_username',columns='id')

In [52]:
common_user_based_matrix.shape

(1319, 108)

In [53]:
# Convert the user_correlation matrix into dataframe.
user_correlation_df = pd.DataFrame(user_correlation)

In [54]:
user_correlation_df['userId'] = df_subtracted.index
user_correlation_df.set_index('userId',inplace=True)
user_correlation_df.head()

0      1      2      3      4      5      6      7      8      \
userId                                                                    
00dog3      1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
00sab00     0.0    1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
01impala    0.0    0.0    1.0    1.0    1.0    0.0    0.0    0.0    0.0   
02dakota    0.0    0.0    1.0    1.0    1.0    0.0    0.0    0.0    0.0   
02deuce     0.0    0.0    1.0    1.0    1.0    0.0    0.0    0.0    0.0   

          9      ...  20520  20521  20522  20523  20524  20525  20526  20527  \
userId           ...                                                           
00dog3      0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
00sab00     0.0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
01impala    0.0  ...    0.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0   
02dakota    0.0  ...    0.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0   
02deuce     0.0  ...    0.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0   

          20528  20529  
userId                  
00dog3      0.0    0.0  
00sab00     1.0    0.0  
01impala    0.0    0.0  
02dakota    0.0    0.0  
02deuce     0.0    0.0  

[5 rows x 20530 columns]

In [56]:

list_name = common.reviews_username.tolist()

user_correlation_df.columns = df_subtracted.index.tolist()

user_correlation_df_1 =  user_correlation_df[user_correlation_df.index.isin(list_name)]
user_correlation_df_2 = user_correlation_df_1.T[user_correlation_df_1.T.index.isin(list_name)]
user_correlation_df_3 = user_correlation_df_2.T

In [57]:
user_correlation_df_3.head()

00sab00      1234  143st     23jen  7inthenest    85lisa  \
userId                                                                 
00sab00         1.0  0.000000    0.0  0.000000    0.000000  0.000000   
1234            0.0  1.000000    0.0  0.575159    0.575159  0.575159   
143st           0.0  0.000000    1.0  0.000000    0.000000  0.000000   
23jen           0.0  0.575159    0.0  1.000000    1.000000  1.000000   
7inthenest      0.0  0.575159    0.0  1.000000    1.000000  1.000000   

            8ellie24  aac06002  abbi  abigail  ...  yayawomack    yellow  \
userId                                         ...                         
00sab00     0.000000       0.0   0.0      0.0  ...         0.0  0.000000   
1234        0.575159       0.0   0.0      0.0  ...         0.0  0.575159   
143st       0.000000       0.0   0.0      0.0  ...         0.0  0.000000   
23jen       1.000000       0.0   0.0      0.0  ...         0.0  1.000000   
7inthenest  1.000000       0.0   0.0      0.0  ...         0.0  1.000000   

            yesseniaw22      ygtz  yoadrian  yummy    yvonne  zburt5  \
userId                                                                 
00sab00             0.0  0.000000  0.000000    0.0  0.000000     0.0   
1234                0.0  0.575159  0.575159    0.0  0.575159     0.0   
143st               0.0  0.000000  0.000000    0.0  0.000000     0.0   
23jen               0.0  1.000000  0.000000    0.0  0.000000     0.0   
7inthenest          0.0  1.000000  0.000000    0.0  0.000000     0.0   

              zebras  zipper  
userId                        
00sab00     0.000000     0.0  
1234        0.575159     0.0  
143st       0.000000     1.0  
23jen       1.000000     0.0  
7inthenest  1.000000     0.0  

[5 rows x 1319 columns]

In [58]:
user_correlation_df_3[user_correlation_df_3<0]=0

common_user_predicted_ratings = np.dot(user_correlation_df_3, common_user_based_matrix.fillna(0))

In [59]:
dummy_test = common.copy()
dummy_test['reviews_rating'] =dummy_test['reviews_rating'].apply(lambda x: 1 if x>=1 else 0)
dummy_test = pd.pivot_table(index='reviews_username',
                            columns='name',
                            values='reviews_rating',data=dummy_test).fillna(0)

In [61]:
common_user_pred_ratings =  np.multiply(common_user_predicted_ratings,dummy_test)
common_user_pred_ratings

name              100:Complete First Season (blu-Ray)  \
reviews_username                                        
00sab00                                           0.0   
1234                                              0.0   
143st                                             0.0   
23jen                                             0.0   
7inthenest                                        0.0   
...                                               ...   
yummy                                             0.0   
yvonne                                            0.0   
zburt5                                            0.0   
zebras                                            0.0   
zipper                                            0.0   

name              Africa's Best No-Lye Dual Conditioning Relaxer System Super  \
reviews_username                                                                
00sab00                                                         0.0             
1234                                                            0.0             
143st                                                           0.0             
23jen                                                           0.0             
7inthenest                                                      0.0             
...                                                             ...             
yummy                                                           0.0             
yvonne                                                          0.0             
zburt5                                                          0.0             
zebras                                                          0.0             
zipper                                                          0.0             

name              Alex Cross (dvdvideo)  \
reviews_username                          
00sab00                             0.0   
1234                                0.0   
143st                               0.0   
23jen                               0.0   
7inthenest                          0.0   
...                                 ...   
yummy                               0.0   
yvonne                              0.0   
zburt5                              0.0   
zebras                              0.0   
zipper                              0.0   

name              All,bran Complete Wheat Flakes, 18 Oz.  \
reviews_username                                           
00sab00                                              0.0   
1234                                                 0.0   
143st                                                0.0   
23jen                                                0.0   
7inthenest                                           0.0   
...                                                  ...   
yummy                                                0.0   
yvonne                                               0.0   
zburt5                                               0.0   
zebras                                               0.0   
zipper                                               0.0   

name              Australian Gold Exotic Blend Lotion, SPF 4  \
reviews_username                                               
00sab00                                                  0.0   
1234                                                     0.0   
143st                                                    0.0   
23jen                                                    0.0   
7inthenest                                               0.0   
...                                                      ...   
yummy                                                    0.0   
yvonne                                                   0.0   
zburt5                                                   0.0   
zebras                                                   0.0   
zipper                                                   0.0   

name              Aveeno Baby 

In [62]:
X  = common_user_pred_ratings.copy()
X = X[X>0]

scaler = MinMaxScaler(feature_range=(1, 5))
print(scaler.fit(X))
y = (scaler.transform(X))

print(y)
y.shape

MinMaxScaler(feature_range=(1, 5))
[[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]


/usr/local/lib/python3.11/dist-packages/sklearn/utils/_array_api.py:776: RuntimeWarning: All-NaN slice encountered
  return xp.asarray(numpy.nanmin(X, axis=axis))
/usr/local/lib/python3.11/dist-packages/sklearn/utils/_array_api.py:793: RuntimeWarning: All-NaN slice encountered
  return xp.asarray(numpy.nanmax(X, axis=axis))


(1319, 108)

In [63]:
total_non_nan = np.count_nonzero(~np.isnan(y))

In [64]:
common_pivot = pd.pivot_table(index='reviews_username',
                            columns='name',
                            values='reviews_rating',data=common)


In [71]:

rmse = np.sqrt(np.nansum((common_pivot - y) ** 2) / total_non_nan)
print("RMSE:", rmse)


RMSE: 2.1665909661064964


Item Item Recomendation

In [72]:
train_pivot_item = dummy_train.T
train_pivot_item


reviews_username      00dog3  00sab00  01impala  02dakota  02deuce  0325home  \
id                                                                             
AV13O1A8GV-KLJ3akUyj     1.0      1.0       1.0       1.0      1.0       1.0   
AV14LG0R-jtxr-f38QfS     1.0      1.0       1.0       1.0      1.0       1.0   
AV16khLE-jtxr-f38VFn     1.0      1.0       1.0       1.0      1.0       1.0   
AV1YGDqsGV-KLJ3adc-O     1.0      1.0       1.0       1.0      1.0       1.0   
AV1YIch7GV-KLJ3addeG     1.0      1.0       1.0       1.0      1.0       1.0   
...                      ...      ...       ...       ...      ...       ...   
AVpfthSailAPnD_xg3ON     1.0      1.0       1.0       1.0      1.0       1.0   
AVpftikC1cnluZ0-p31V     1.0      1.0       1.0       1.0      1.0       1.0   
AVpftymALJeJML43CZ6y     1.0      1.0       1.0       1.0      1.0       1.0   
AVpfv4TlilAPnD_xhjNS     1.0      1.0       1.0       1.0      1.0       1.0   
AVpfvieo1cnluZ0-qdnu     1.0      1.0       1.0       1.0      1.0       1.0   

reviews_username      06stidriver  08dallas  09mommy11  1.11E+24  ...  zpalma  \
id                                                                ...           
AV13O1A8GV-KLJ3akUyj          1.0       1.0        1.0       1.0  ...     1.0   
AV14LG0R-jtxr-f38QfS          1.0       1.0        1.0       1.0  ...     1.0   
AV16khLE-jtxr-f38VFn          1.0       1.0        1.0       1.0  ...     1.0   
AV1YGDqsGV-KLJ3adc-O          1.0       1.0        1.0       1.0  ...     1.0   
AV1YIch7GV-KLJ3addeG          1.0       1.0        1.0       1.0  ...     1.0   
...                           ...       ...        ...       ...  ...     ...   
AVpfthSailAPnD_xg3ON          1.0       1.0        1.0       1.0  ...     1.0   
AVpftikC1cnluZ0-p31V          1.0       1.0        1.0       1.0  ...     1.0   
AVpftymALJeJML43CZ6y          1.0       1.0        1.0       1.0  ...     1.0   
AVpfv4TlilAPnD_xhjNS          1.0       1.0        1.0       1.0  ...     1.0   
AVpfvieo1cnluZ0-qdnu          1.0       1.0        1.0       1.0  ...     1.0   

reviews_username      zsazsa  zt313  zubb  zulaa118  zuttle  zxcsdfd  zxjki  \
id                                                                            
AV13O1A8GV-KLJ3akUyj     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AV14LG0R-jtxr-f38QfS     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AV16khLE-jtxr-f38VFn     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AV1YGDqsGV-KLJ3adc-O     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AV1YIch7GV-KLJ3addeG     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
...                      ...    ...   ...       ...     ...      ...    ...   
AVpfthSailAPnD_xg3ON     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AVpftikC1cnluZ0-p31V     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AVpftymALJeJML43CZ6y     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AVpfv4TlilAPnD_xhjNS     1.0    1.0   1.0       1.0     1.0      1.0    1.0   
AVpfvieo1cnluZ0-qdnu     1.0    1.0   1.0       1.0     1.0      1.0    1.0   

reviews_username      zzdiane  zzz1127  
id                                      
AV13O1A8GV-KLJ3akUyj      1.0      1.0  
AV14LG0R-jtxr-f38QfS      1.0      1.0  
AV16khLE-jtxr-f38VFn      1.0      1.0  
AV1YGDqsGV-KLJ3adc-O      1.0      1.0  
AV1YIch7GV-KLJ3addeG      1.0      1.0  
...                       ...      ...  
AVpfthSailAPnD_xg3ON      1.0      1.0  
AVpftikC1cnluZ0-p31V      1.0      1.0  
AVpftymALJeJML43CZ6y      1.0      1.0  
AVpfv4TlilAPnD_xhjNS      1.0      1.0  
AVpfvieo1cnluZ0-qdnu      1.0      1.0  

[265 rows x 20530 columns]

In [73]:
item_correlation = 1 - pairwise_distances(train_pivot_item, metric='cosine')
item_correlation[np.isnan(item_correlation)] = 0
print(item_correlation)

[[1.         0.99922156 0.9964493  ... 0.99922156 0.99912445 0.99649587]
 [0.99922156 1.         0.9964493  ... 0.99922156 0.99912445 0.99649587]
 [0.9964493  0.9964493  1.         ... 0.9964493  0.9963523  0.99372892]
 ...
 [0.99922156 0.99922156 0.9964493  ... 1.         0.99912445 0.99649587]
 [0.99912445 0.99912445 0.9963523  ... 0.99912445 1.         0.99639888]
 [0.99649587 0.99649587 0.99372892 ... 0.99649587 0.99639888 1.        ]]


In [ ]:
item_correlation[item_correlation < 0] = 0

In [ ]:
item_pred_ratings = np.dot(item_correlation,train_pivot_item.fillna(0))

In [ ]:
item_final_rating = np.multiply(item_pred_rating,df_pivot)
item_final_rating

In [ ]:
user_input = "00dog3"
recommendations = item_final_rating.loc[user_input].sort_values(ascending=False)[0:20]
recommendations

id
AVpe6FfKilAPnD_xQmHi    79038.274725
AVpf3VOfilAPnD_xjpun    42618.433141
AVpfPaoqLJeJML435Xk9    27770.477509
AVpfJP1C1cnluZ0-e3Xy    25297.869620
AVpfRTh1ilAPnD_xYic2    22841.202143
AVpf63aJLJeJML43F__Q    22147.926864
AVpf0eb2LJeJML43EVSt    22006.639988
AVpfW8y_LJeJML437ySW    21829.260335
AVpf2tw1ilAPnD_xjflC    21558.523946
AVpe41TqilAPnD_xQH3d    21537.206999
AV1l8zRZvKc47QAVhnAv    21493.556337
AVpe59io1cnluZ0-ZgDU    21423.638781
AVpf9pzn1cnluZ0-uNTM    20817.258883
AVpe9W4D1cnluZ0-avf0    20549.447180
AV1YGDqsGV-KLJ3adc-O    20501.934805
AVpf4oLxLJeJML43FcxC    20492.014365
AVpe8gsILJeJML43y6Ed    20452.728224
AVpftikC1cnluZ0-p31V    20367.405412
AVpfM_ytilAPnD_xXIJb    20364.331163
AVpe31o71cnluZ0-YrSD    20295.168996
Name: 00dog3, dtype: float64

RMSE Calculation

In [ ]:
common = test[test.reviews_username.isin(train.reviews_username)]
common.shape

In [ ]:
common.head()

In [ ]:
common_item_based_matrix=  pd.pivot_table(data=common,values='reviews_rating',index='reviews_username',columns='id')


In [1]:
# Convert the item_correlation matrix into dataframe.
item_correlation_df = pd.DataFrame(item_correlation)

NameError: name 'pd' is not defined

In [ ]:
user_correlation_df['userId'] = df_subtracted.index
user_correlation_df.set_index('userId',inplace=True)
user_correlation_df.head()

In [ ]:
item_corr_df['name'] = normalized_item_df.index
item_corr_df.set_index('name',inplace=True)

In [ ]:
list_items = common_item.name.tolist()
item_corr_df.columns = normalized_item_df.index.tolist()

In [ ]:
item_corr_df1 = item_corr_df[item_corr_df.index.isin(list_items)]

In [ ]:
item_corr_df2 = item_corr_df1.T[item_corr_df1.T.index.isin(list_items)]
item_corr_df3 = item_corr_df2.T

In [ ]:
item_corr_df3[item_corr_df3<0] = 0
common_item_pred_ratings = np.dot(item_corr_df3,common_item_pivot.fillna(0))

In [ ]:
test_items = common_item.copy()

In [ ]:
test_item_tb = test_items.pivot_table(index='reviews_username',
                            columns='name',
                            values='reviews_rating').T.fillna(0)
final_item_ratings = np.multiply(common_item_pred_ratings,test_item_tb)
final_item_ratings

In [ ]:
X  = final_item_ratings.copy()
X = X[X>0]

scaler = MinMaxScaler(feature_range=(1, 5))
print(scaler.fit(X))
y = (scaler.transform(X))

print(y)
y.shape

In [ ]:
total_non_nan = np.count_nonzero(~np.isnan(y))

In [ ]:

rmse = np.sqrt(np.nansum((common_pivot - y) ** 2) / total_non_nan)
print("RMSE:", rmse)

Deciding User-User or Item-Item Recommendation: Which is better?

**Recommendation of Top 20 Products to a Specified User**